In [115]:
import re
import requests
import unicodedata
from bs4 import BeautifulSoup

In [117]:
#define the endpoint
endpoint = r"https://www.sec.gov/cgi-bin/browse-edgar"

# define parameters
param_dict = {"action": "getcompany",
             "CIK": "MSFT",
             "type": "10-k",
             #"dateb": "20190101",
             "owner": "exclude",
             "start": "",
             "output": "atom",
             "count": "100"}

# define response
response = requests.get(url = endpoint, params = param_dict)
soup = BeautifulSoup(response.content, "lxml")

soup

<?xml version="1.0" encoding="ISO-8859-1" ?><html><body><feed xmlns="http://www.w3.org/2005/Atom">
<author>
<email>webmaster@sec.gov</email>
<name>Webmaster</name>
</author>
<company-info>
<addresses>
<address type="mailing">
<city>REDMOND</city>
<state>WA</state>
<street1>ONE MICROSOFT WAY</street1>
<zip>98052-6399</zip>
</address>
<address type="business">
<city>REDMOND</city>
<phone>425-882-8080</phone>
<state>WA</state>
<street1>ONE MICROSOFT WAY</street1>
<zip>98052-6399</zip>
</address>
</addresses>
<assigned-sic>7372</assigned-sic>
<assigned-sic-desc>SERVICES-PREPACKAGED SOFTWARE</assigned-sic-desc>
<assigned-sic-href>https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&amp;SIC=7372&amp;owner=exclude&amp;count=100</assigned-sic-href>
<cik>0000789019</cik>
<cik-href>https://www.sec.gov/cgi-bin/browse-edgar?action=getcompany&amp;CIK=0000789019&amp;owner=exclude&amp;count=100</cik-href>
<conformed-name>MICROSOFT CORP</conformed-name>
<fiscal-year-end>0630</fiscal-year-end>
<o

In [116]:
# Function to normalize the text
def restore_windows_1252_characters(restore_string):
    def to_windows_1252(match):
        try:
            return bytes([ord(match.group(0))]).decode("windows-1252")
        except UnicodeDecodeError:
            return " "
    
    return re.sub(r'[\u0080-\u0099]', to_windows, restore_string)

In [119]:
# define the url to a specific text file
new_html_text = r"http://www.sec.gov/Archives/edgar/data/1166036/000110465904027382/0001104659-04-027382.txt"

# grb the response
response = requests.get(new_html_text)

# parse the response
soup = BeautifulSoup(response.content, "lxml")
soup

<html><body><p>-----BEGIN PRIVACY-ENHANCED MESSAGE-----
Proc-Type: 2001,MIC-CLEAR
Originator-Name: webmaster@www.sec.gov
Originator-Key-Asymmetric:
 MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen
 TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB
MIC-Info: RSA-MD5,RSA,
 Qv2jQwkNcHK0jmh1uw9JmsapJjhSCceQJLdEQsrmZh5YPKB2tMIC07tAARLtOJNv
 RF+yO70MOHHbXjXQABtM/g==

<sec-document>0001104659-04-027382.txt : 20040913
<sec-header>0001104659-04-027382.hdr.sgml : 20040913
<acceptance-datetime>20040913074905
ACCESSION NUMBER:		0001104659-04-027382
CONFORMED SUBMISSION TYPE:	8-K/A
PUBLIC DOCUMENT COUNT:		7
CONFORMED PERIOD OF REPORT:	20040730
ITEM INFORMATION:		Completion of Acquisition or Disposition of Assets
ITEM INFORMATION:		Financial Statements and Exhibits
FILED AS OF DATE:		20040913
DATE AS OF CHANGE:		20040913

FILER:

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			MARKWEST ENERGY PARTNERS L P
		CENTRAL INDEX KEY:			0001166036
		STANDARD INDUSTRIAL CLASSIFICATION:	CRU

In [120]:
# define a new dictionary to house filings
master_filings_dict = {}

# define a unique key for each filename
accession_number = "0001104659-04-027382"

# add the key to the dict and add a new level
master_filings_dict[accession_number] = {}

# add the next levels
master_filings_dict[accession_number]["sec_header_content"] = {}
master_filings_dict[accession_number]["filing_documtents"] = None

In [122]:
# grab the sec-header document
sec_header_tag = soup.find('sec-header')

#store the sec header content inside the dictionary
master_filings_dict[accession_number]["sec_header_content"]["sec_header_code"] = sec_header_tag

sec_header_tag

<sec-header>0001104659-04-027382.hdr.sgml : 20040913
<acceptance-datetime>20040913074905
ACCESSION NUMBER:		0001104659-04-027382
CONFORMED SUBMISSION TYPE:	8-K/A
PUBLIC DOCUMENT COUNT:		7
CONFORMED PERIOD OF REPORT:	20040730
ITEM INFORMATION:		Completion of Acquisition or Disposition of Assets
ITEM INFORMATION:		Financial Statements and Exhibits
FILED AS OF DATE:		20040913
DATE AS OF CHANGE:		20040913

FILER:

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			MARKWEST ENERGY PARTNERS L P
		CENTRAL INDEX KEY:			0001166036
		STANDARD INDUSTRIAL CLASSIFICATION:	CRUDE PETROLEUM &amp; NATURAL GAS [1311]
		IRS NUMBER:				270005456
		FISCAL YEAR END:			1231

	FILING VALUES:
		FORM TYPE:		8-K/A
		SEC ACT:		1934 Act
		SEC FILE NUMBER:	001-31239
		FILM NUMBER:		041026639

	BUSINESS ADDRESS:	
		STREET 1:		155 INVERNESS DR WEST
		STREET 2:		STE 200
		CITY:			ENGLEWOOD
		STATE:			CO
		ZIP:			80112
		BUSINESS PHONE:		303-925-9275

	MAIL ADDRESS:	
		STREET 1:		155 INVERNESS DR WEST
		STREET 2:		STE 200
		C

In [124]:
# initialize master document dictionary
master_document_dict = {}

# loop through each document in the filing
for filing_document in soup.find_all('document'):
    
    # define my document id
    document_id = filing_document.type.find(text=True, recursive = False).strip()
    
    print(document_id)

8-K/A
EX-2.1
EX-4.1
EX-4.2
EX-23.1
EX-99.1
EX-99.2
